In [0]:
dbutils.fs.mount(
  source = "wasbs://silver@ilab9788543873.blob.core.windows.net",
  mount_point = "/mnt/ilab9788543873/silver",
  extra_configs = {"fs.azure.account.key.ilab9788543873.blob.core.windows.net":"TAyrrfaiCQ86vkgSXyStufowrMVdk4T45mVw6TNcFFJocR6pTXy6ZMSUUTeeh5FpNTsBVAbVqdwk+AStHA3x1g=="})

True

In [0]:
dbutils.fs.unmount("/mnt/ilab9788543873/silver/")


/mnt/ilab9788543873/silver/ has been unmounted.


True

In [0]:
%fs ls /mnt/ilab9788543873/silver/

path name size modificationTime dbfs:/mnt/ilab9788543873/silver/abstract.parquet abstract.parquet 3852887 1697695355000 dbfs:/mnt/ilab9788543873/silver/applicants.parquet applicants.parquet 323669 1697695334000 dbfs:/mnt/ilab9788543873/silver/biblio_cited_by.parquet biblio_cited_by.parquet 735953 1697695335000 dbfs:/mnt/ilab9788543873/silver/claims.parquet claims.parquet 23921603 1697695345000 dbfs:/mnt/ilab9788543873/silver/classifications.parquet classifications.parquet 764314 1697695335000 dbfs:/mnt/ilab9788543873/silver/descriptions.parquet descriptions.parquet 297863908 1697695471000 dbfs:/mnt/ilab9788543873/silver/earliest_claim.parquet earliest_claim.parquet 247195 1697695337000 dbfs:/mnt/ilab9788543873/silver/invention_title.parquet invention_title.parquet 947103 1697695339000 dbfs:/mnt/ilab9788543873/silver/inventors.parquet inventors.parquet 526520 1697695341000 dbfs:/mnt/ilab9788543873/silver/legal_status.parquet legal_status.parquet 237066 1697695344000 dbfs:/mnt/ilab9788543873/silver/main.parquet main.parquet 339606 1697695334000 dbfs:/mnt/ilab9788543873/silver/merged_df.parquet/ merged_df.parquet/ 0 1697704506000 dbfs:/mnt/ilab9788543873/silver/owners_all.parquet owners_all.parquet 298250 1697695334000 dbfs:/mnt/ilab9788543873/silver/priority_claims.parquet priority_claims.parquet 461547 1697695335000 dbfs:/mnt/ilab9788543873/silver/publication_reference.parquet publication_reference.parquet 338986 1697695334000 dbfs:/mnt/ilab9788543873/silver/references_cited.parquet references_cited.parquet 537244 1697695334000

In [0]:
# Load parquet files into DataFrames
abstract_df = spark.read.parquet("/mnt/ilab9788543873/silver/abstract.parquet")
applicants_df = spark.read.parquet("/mnt/ilab9788543873/silver/applicants.parquet")
biblio_cited_by_df = spark.read.parquet("/mnt/ilab9788543873/silver/biblio_cited_by.parquet")
claims_df = spark.read.parquet("/mnt/ilab9788543873/silver/claims.parquet")
classifications_df = spark.read.parquet("/mnt/ilab9788543873/silver/classifications.parquet")
descriptions_df = spark.read.parquet("/mnt/ilab9788543873/silver/descriptions.parquet")
earliest_claim_df = spark.read.parquet("/mnt/ilab9788543873/silver/earliest_claim.parquet")
invention_title_df = spark.read.parquet("/mnt/ilab9788543873/silver/invention_title.parquet")
inventors_df = spark.read.parquet("/mnt/ilab9788543873/silver/inventors.parquet")
legal_status_df = spark.read.parquet("/mnt/ilab9788543873/silver/legal_status.parquet")
main_df = spark.read.parquet("/mnt/ilab9788543873/silver/main.parquet")
owners_all_df = spark.read.parquet("/mnt/ilab9788543873/silver/owners_all.parquet")
priority_claims_df = spark.read.parquet("/mnt/ilab9788543873/silver/priority_claims.parquet")
references_cited_df = spark.read.parquet("/mnt/ilab9788543873/silver/references_cited.parquet")
publication_reference_df = spark.read.parquet("/mnt/ilab9788543873/silver/publication_reference.parquet")


In [0]:
from pyspark.sql import functions as F

# Merge the dataframes
merged_df = main_df.join(abstract_df, ["lens_id"], "left_outer")\
                   .join(applicants_df, ["lens_id"], "left_outer")\
                   .join(biblio_cited_by_df, ["lens_id"], "left_outer")\
                   .join(claims_df, ["lens_id"], "left_outer")\
                   .join(classifications_df, ["lens_id"], "left_outer")\
                   .join(descriptions_df, ["lens_id"], "left_outer")\
                   .join(earliest_claim_df, ["lens_id"], "left_outer")\
                   .join(invention_title_df, ["lens_id"], "left_outer")\
                   .join(inventors_df, ["lens_id"], "left_outer")\
                   .join(legal_status_df, ["lens_id"], "left_outer")\
                   .join(owners_all_df, ["lens_id"], "left_outer")\
                   .join(priority_claims_df, ["lens_id"], "left_outer")\
                   .join(references_cited_df, ["lens_id"], "left_outer")\
                   .join(publication_reference_df, ["lens_id"], "left_outer")



In [0]:
# List of columns
cols = merged_df.columns

# Rename columns based on their positions
cols[29] = 'priority_claims_doc_number'
cols[42] = 'publication_reference_doc_number'

cols[28] = 'priority_claims_jurisdiction'
cols[41] = 'publication_ref_jurisdiction'

cols[30] = 'priority_claims_kind'
cols[43] = 'publication_ref_kind'

cols[17] = 'earliest_claim_date'
cols[27] = 'priority_claims_date'
cols[44] = 'publication_reference_date'

cols[32] = 'priority_claims_sequence'
cols[34] = 'reference_cited_sequence'

# Apply the new column names to the DataFrame
merged_df = merged_df.toDF(*cols)


In [0]:
# List of columns to drop based on the analysis
columns_to_drop = [
    "applicant_name",
    "owner_name",
    "address",
    "execution_date",
    "priority_claims_date",
    "priority_claims_jurisdiction",
    "priority_claims_doc_number",
    "priority_claims_kind",
    "date",
    "priority_claims_sequence",
    "cited_phase",
    "reference_cited_sequence",
    "0",
    "lang" 
]

# Drop the columns from the DataFrame
merged_df_cleaned = merged_df.drop(*columns_to_drop)


In [0]:
merged_df_cleaned.printSchema()


root
 |-- lens_id: string (nullable = true)
 |-- date_published: string (nullable = true)
 |-- doc_number: string (nullable = true)
 |-- jurisdiction: string (nullable = true)
 |-- kind: string (nullable = true)
 |-- text: string (nullable = true)
 |-- patent_count: double (nullable = true)
 |-- cited_lens_id: string (nullable = true)
 |-- cited_jurisdiction: string (nullable = true)
 |-- cited_doc_number: string (nullable = true)
 |-- cited_kind: string (nullable = true)
 |-- claim_text: string (nullable = true)
 |-- symbol: string (nullable = true)
 |-- description_text: string (nullable = true)
 |-- earliest_claim_date: string (nullable = true)
 |-- invention_title: string (nullable = true)
 |-- inventor_name: string (nullable = true)
 |-- grant_date: string (nullable = true)
 |-- granted: boolean (nullable = true)
 |-- patent_status: string (nullable = true)
 |-- country: string (nullable = true)
 |-- nplcit_lens_id: string (nullable = true)
 |-- nplcit_text: string (nullable = tru

In [0]:
display(merged_df)

lens_id date_published doc_number jurisdiction kind lang text applicant_name patent_count cited_lens_id cited_jurisdiction cited_doc_number cited_kind 0 claim_text symbol description_text earliest_claim_date invention_title inventor_name grant_date granted patent_status owner_name address country execution_date priority_claims_date jurisdiction doc_number kind earliest_claim_date sequence cited_phase sequence nplcit_lens_id nplcit_text patcit_jurisdiction patcit_doc_number patcit_kind patcit_date jurisdiction doc_number kind publication_reference_date 199-441-098-963-068 2019-10-10 20190313471 US A1 en A UE may receive, via a first communication link that uses a first radio access technology (RAT), information that identifies a threshold associated with a second communication link that uses a second RAT. The UE may monitor one or more communications on the second communication link. The UE may determine whether a parameter associated with the second communication link satisfies the threshold based at least in part on monitoring the one or more communications on the second communication link. The UE may provide a message via the first communication link when the parameter associated with the second communication link satisfies the threshold. MICROSOFT TECHNOLOGY LICENSING LLC null null null null null null 30 . The base station of claim 27 , wherein the one or more processors are configured to receive a notification when the UE establishes a second communication link to a serving access point of the list of access point identifiers of access points that use the second RAT and to which the UE is permitted to connect. G06F11/0727 CLAIM OF PRIORITY UNDER 35 U.S.C. § 120 The present application for patent is continuation of U.S. patent application Ser. No. 16/008,443, entitled “TECHNIQUES FOR MANAGING COMMUNICATION LINKS OF A PLURALITY OF RADIO ACCESS TECHNOLOGIES (RATS)” filed Jun. 14, 2018, which is a divisional of U.S. patent application Ser. No. 15/152,278, entitled “TECHNIQUES FOR MANAGING COMMUNICATION LINKS OF A PLURALITY OF RADIO ACCESS TECHNOLOGIES (RATS)” filed May 11, 2016, which claims priority to U.S. Provisional Application No. 62/162,533, entitled “TECHNIQUES FOR MANAGING COMMUNICATION LINKS OF A PLURALITY OF RADIO ACCESS TECHNOLOGIES (RATS)” filed May 15, 2015, each of which is assigned to the assignee hereof and hereby expressly incorporated by reference herein. FIELD OF THE DISCLOSURE Aspects of the present disclosure relate generally to wireless communications, and more particularly, to techniques for managing communication links of a plurality of radio access technologies (RATs). BACKGROUND Wireless communication systems are widely deployed to provide various types of communication content, such as voice, video, packet data, messaging, broadcast, or the like. These systems may be multiple-access systems capable of supporting communication with multiple users by sharing the available system resources (e.g., time, frequency, and power). Examples of such multiple-access systems include code-division multiple access (CDMA) systems, time-division multiple access (TDMA) systems, frequency-division multiple access (FDMA) systems, and orthogonal frequency-division multiple access (OFDMA) systems. By way of example, a wireless multiple-access communication system may include a number of base stations, each simultaneously supporting communication for multiple communication devices, otherwise known as user equipment (UEs). A base station may communicate with UEs on downlink channels (e.g., for transmissions from a base station to a UE) and uplink channels (e.g., for transmissions from a UE to a base station). The wireless communications with a UE or a network device (e.g., base station, eNodeB) may take place over two separate radio access technologies (RATs), where the first RAT may correspond to a WWAN RAT (e.g., Long Term Evolution (LTE)) and the second RAT may correspond to a wireless local area network (WLAN) RAT (e.g.

In [0]:
merged_df_cleaned.count()

685113

In [0]:
# Drop uneeded columns
new_main_df = main_df.drop("doc_number", "lang")

In [0]:
# Store new_main_df
new_main_df.write.mode("overwrite").parquet("/mnt/ilab9788543873/silver/new_main_df.parquet")

In [0]:
new_main_df = spark.read.parquet("/mnt/ilab9788543873/silver/new_main_df.parquet")

In [0]:
from pyspark.sql import functions as F

# Start merging
merged_df = new_main_df.join(abstract_df, ["lens_id"], "left_outer")

In [0]:
# Store merged df
merged_df.write.mode("overwrite").parquet("/mnt/ilab9788543873/silver/merged_df.parquet")

In [0]:
merged_df = spark.read.parquet("/mnt/ilab9788543873/silver/merged_df.parquet")

In [0]:
merged_df = merged_df.join(applicants_df, ["lens_id"], "left_outer")

In [0]:
# Store merged df
merged_df.write.mode("overwrite").parquet("/mnt/ilab9788543873/silver/merged_df2.parquet")

In [0]:
merged_df = spark.read.parquet("/mnt/ilab9788543873/silver/merged_df2.parquet")

In [0]:
# Drop uneeded columns
new_biblio_cited_by_df = biblio_cited_by_df.drop("cited_doc_number", "0")

In [0]:
merged_df = merged_df.join(new_biblio_cited_by_df, ["lens_id"], "left_outer")

In [0]:
# Store merged df
merged_df.write.mode("overwrite").parquet("/mnt/ilab9788543873/silver/merged_df3.parquet")

In [0]:
merged_df = spark.read.parquet("/mnt/ilab9788543873/silver/merged_df3.parquet")

In [0]:
merged_df = merged_df.join(claims_df, ["lens_id"], "left_outer")\
    .join(classifications_df, ["lens_id"], "left_outer")

In [0]:
# Store merged df
merged_df.write.mode("overwrite").parquet("/mnt/ilab9788543873/silver/merged_df4.parquet")

In [0]:
merged_df = spark.read.parquet("/mnt/ilab9788543873/silver/merged_df4.parquet")

In [0]:
merged_df = merged_df.join(earliest_claim_df, ["lens_id"], "left_outer")

In [0]:
# Store merged df
merged_df.write.mode("overwrite").parquet("/mnt/ilab9788543873/silver/merged_df5.parquet")

In [0]:
merged_df = spark.read.parquet("/mnt/ilab9788543873/silver/merged_df5.parquet")

In [0]:
merged_df = merged_df.join(invention_title_df, ["lens_id"], "left_outer")

In [0]:
# Store merged df
merged_df.write.mode("overwrite").parquet("/mnt/ilab9788543873/silver/merged_df6.parquet")

In [0]:
merged_df = spark.read.parquet("/mnt/ilab9788543873/silver/merged_df6.parquet")

In [0]:
merged_df.count()

685113

In [0]:
merged_df = merged_df.join(inventors_df, ["lens_id"], "left_outer")

In [0]:
# Store merged df
merged_df.write.mode("overwrite").parquet("/mnt/ilab9788543873/silver/merged_df7.parquet")

In [0]:
merged_df = spark.read.parquet("/mnt/ilab9788543873/silver/merged_df7.parquet")

In [0]:
merged_df = merged_df.join(legal_status_df, ["lens_id"], "left_outer")

In [0]:
# Store merged df
merged_df.write.mode("overwrite").parquet("/mnt/ilab9788543873/silver/merged_df8.parquet")

In [0]:
merged_df = spark.read.parquet("/mnt/ilab9788543873/silver/merged_df8.parquet")

In [0]:
# Drop uneeded columns
new_references_cited_df = references_cited_df.drop("patcit_doc_number", "patcit_date")

In [0]:
new_references_cited_df.write.mode("overwrite").parquet("/mnt/ilab9788543873/silver/new_references_cited_df.parquet")

In [0]:
new_references_cited_df = spark.read.parquet("/mnt/ilab9788543873/silver/new_references_cited_df.parquet")

In [0]:
merged_df = merged_df.join(new_references_cited_df, ["lens_id"], "left_outer")

In [0]:
# Store merged df
merged_df.write.mode("overwrite").parquet("/mnt/ilab9788543873/silver/merged_df9.parquet")

In [0]:
merged_df = spark.read.parquet("/mnt/ilab9788543873/silver/merged_df9.parquet")

In [0]:
display(merged_df)

lens_id date_published jurisdiction kind text applicant_name patent_count cited_lens_id cited_jurisdiction cited_kind claim_text symbol date invention_title inventor_name grant_date granted patent_status cited_phase sequence nplcit_lens_id nplcit_text patcit_jurisdiction patcit_kind 062-048-831-816-441 2019-12-17 US B2 Data values for various items are visualized in real-time or near real-time using radial-based techniques to produce data visualizations bearing some resemblance to, for example, pie charts, radial charts, etc. The data values are shown using indicators that encircle, or at least partially encircle, a central point. One or more characteristics of the indicator reflect the value that corresponds to the indicator. The characteristics may include, for instance, the color of the indicator and/or the distance of the indicator (or more specifically, a given point on the indicator) from the central point. The characteristics of the indicators change over time, in accordance with changes in the current values of the data items. A variety of indicators may be used, including, without limitation, points, icons, pie “wedges,” filled or partially-filled sectors of an ellipse or semi-circle, arcs or lines that span between the sides of such sectors, and so forth. IBM 2.0 034-584-922-278-697 US B2 1. A method, comprising: receiving a set of data values from one or more data sources; causing display of the set of data values in a radial graph comprising a circular region having sectors with a common vertex, wherein each sector includes a radial projection that fills the sector extending from the common vertex to a level in the sector determined by mapping a corresponding data value in the set of data values to a fixed scale for the radial graph; and upon receiving substantially real-time updates to one or more data values in the set of data values that correspond to a particular radial projection, dynamically modifying the fill of that radial projection within the corresponding sector to a level that reflects the changes in the one or more data values while maintaining the fixed scale for the radial graph. H04L47/125 2013-07-31 TECHNOLOGIES FOR SHARING PACKET REPLICATION RESOURCES IN A SWITCHING SYSTEM CAKULEV VIOLETA 2019-12-17 true ACTIVE APP 23.0 null null US A1 062-048-831-816-441 2019-12-17 US B2 Data values for various items are visualized in real-time or near real-time using radial-based techniques to produce data visualizations bearing some resemblance to, for example, pie charts, radial charts, etc. The data values are shown using indicators that encircle, or at least partially encircle, a central point. One or more characteristics of the indicator reflect the value that corresponds to the indicator. The characteristics may include, for instance, the color of the indicator and/or the distance of the indicator (or more specifically, a given point on the indicator) from the central point. The characteristics of the indicators change over time, in accordance with changes in the current values of the data items. A variety of indicators may be used, including, without limitation, points, icons, pie “wedges,” filled or partially-filled sectors of an ellipse or semi-circle, arcs or lines that span between the sides of such sectors, and so forth. IBM 2.0 034-584-922-278-697 US B2 2. The method of claim 1 , wherein a radial projection for a sector comprises a sub-sector having a radius representing the corresponding data value for the radial projection. H04L47/125 2013-07-31 TECHNOLOGIES FOR SHARING PACKET REPLICATION RESOURCES IN A SWITCHING SYSTEM CAKULEV VIOLETA 2019-12-17 true ACTIVE APP 23.0 null null US A1 062-048-831-816-441 2019-12-17 US B2 Data values for various items are visualized in real-time or near real-time using radial-based techniques to produce data visualizations bearing some resemblance to, for example, pie charts, radial charts, etc. The data values are shown using indicators that encircle, or at least pa

In [0]:
# Store merged df
merged_df.write.mode("overwrite").parquet("/mnt/ilab9788543873/gold/df.parquet")

In [0]:
%fs ls /mnt/ilab9788543873/silver/

path name size modificationTime dbfs:/mnt/ilab9788543873/silver/abstract.parquet abstract.parquet 3852887 1697695355000 dbfs:/mnt/ilab9788543873/silver/applicants.parquet applicants.parquet 323669 1697695334000 dbfs:/mnt/ilab9788543873/silver/biblio_cited_by.parquet biblio_cited_by.parquet 735953 1697695335000 dbfs:/mnt/ilab9788543873/silver/claims.parquet claims.parquet 23921603 1697695345000 dbfs:/mnt/ilab9788543873/silver/classifications.parquet classifications.parquet 764314 1697695335000 dbfs:/mnt/ilab9788543873/silver/descriptions.parquet descriptions.parquet 297863908 1697695471000 dbfs:/mnt/ilab9788543873/silver/earliest_claim.parquet earliest_claim.parquet 247195 1697695337000 dbfs:/mnt/ilab9788543873/silver/invention_title.parquet invention_title.parquet 947103 1697695339000 dbfs:/mnt/ilab9788543873/silver/inventors.parquet inventors.parquet 526520 1697695341000 dbfs:/mnt/ilab9788543873/silver/legal_status.parquet legal_status.parquet 237066 1697695344000 dbfs:/mnt/ilab9788543873/silver/main.parquet main.parquet 339606 1697695334000 dbfs:/mnt/ilab9788543873/silver/merged_df.parquet/ merged_df.parquet/ 0 1697705461000 dbfs:/mnt/ilab9788543873/silver/merged_df10.parquet/ merged_df10.parquet/ 0 1697710359000 dbfs:/mnt/ilab9788543873/silver/merged_df2.parquet/ merged_df2.parquet/ 0 1697705602000 dbfs:/mnt/ilab9788543873/silver/merged_df3.parquet/ merged_df3.parquet/ 0 1697705797000 dbfs:/mnt/ilab9788543873/silver/merged_df4.parquet/ merged_df4.parquet/ 0 1697706002000 dbfs:/mnt/ilab9788543873/silver/merged_df5.parquet/ merged_df5.parquet/ 0 1697706676000 dbfs:/mnt/ilab9788543873/silver/merged_df6.parquet/ merged_df6.parquet/ 0 1697706857000 dbfs:/mnt/ilab9788543873/silver/merged_df7.parquet/ merged_df7.parquet/ 0 1697707130000 dbfs:/mnt/ilab9788543873/silver/merged_df8.parquet/ merged_df8.parquet/ 0 1697707438000 dbfs:/mnt/ilab9788543873/silver/merged_df9.parquet/ merged_df9.parquet/ 0 1697711642000 dbfs:/mnt/ilab9788543873/silver/merged_df_cleaned.parquet/ merged_df_cleaned.parquet/ 0 1697705257000 dbfs:/mnt/ilab9788543873/silver/new_main_df.parquet/ new_main_df.parquet/ 0 1697705361000 dbfs:/mnt/ilab9788543873/silver/new_references_cited_df.parquet/ new_references_cited_df.parquet/ 0 1697708412000 dbfs:/mnt/ilab9788543873/silver/owners_all.parquet owners_all.parquet 298250 1697695334000 dbfs:/mnt/ilab9788543873/silver/priority_claims.parquet priority_claims.parquet 461547 1697695335000 dbfs:/mnt/ilab9788543873/silver/publication_reference.parquet publication_reference.parquet 338986 1697695334000 dbfs:/mnt/ilab9788543873/silver/references_cited.parquet references_cited.parquet 537244 1697695334000

In [0]:
pip install --upgrade azure-storage-blob

Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.
Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.


In [0]:
spark.conf.set(
  "spark.hadoop.fs.azure", 
  "org.apache.hadoop.fs.azure.NativeAzureFileSystem"
)
spark.conf.set(
  "spark.hadoop.fs.azure.account.key.ilab9788543873.blob.core.windows.net",
  "TAyrrfaiCQ86vkgSXyStufowrMVdk4T45mVw6TNcFFJocR6pTXy6ZMSUUTeeh5FpNTsBVAbVqdwk+AStHA3x1g=="
)

In [0]:
from pyspark.sql import SparkSession

# Replace these with your actual Azure Storage account name and access key
account_name = 'ilab9788543873'
account_key = 'TAyrrfaiCQ86vkgSXyStufowrMVdk4T45mVw6TNcFFJocR6pTXy6ZMSUUTeeh5FpNTsBVAbVqdwk+AStHA3x1g=='

# Initialize a Spark session
spark = SparkSession.builder.appName("AzureBlobStorageExample").getOrCreate()

# Define the Azure Blob Storage container and path
container = "gold"
path = f"wasbs://{container}@{account_name}.blob.core.windows.net/merged_df.parquet"

# Assuming 'merged_df' is your DataFrame, you can write it to the specified path
merged_df.write.parquet(path)

# Stop the Spark session when you're done
spark.stop()

---------------------------------------------------------------------------
Py4JJavaError                             Traceback (most recent call last)
File <command-2071015666366386>, line 15
     12 path = f"wasbs://{container}@{account_name}.blob.core.windows.net/merged_df.parquet"
     14 # Assuming 'merged_df' is your DataFrame, you can write it to the specified path
---> 15 merged_df.write.parquet(path)
     17 # Stop the Spark session when you're done
     18 spark.stop()

File /databricks/spark/python/pyspark/instrumentation_utils.py:48, in _wrap_function.<locals>.wrapper(*args, **kwargs)
     46 start = time.perf_counter()
     47 try:
---> 48     res = func(*args, **kwargs)
     49     logger.log_success(
     50         module_name, class_name, function_name, time.perf_counter() - start, signature
     51     )
     52     return res

File /databricks/spark/python/pyspark/sql/readwriter.py:1721, in DataFrameWriter.parquet(self, path, mode, partitionBy, compression)
   1719  

In [0]:
dbutils.fs.mount(
  source = "wasbs://gold@ilab9788543873.blob.core.windows.net",
  mount_point = "/mnt/ilab9788543873/gold",
  extra_configs = {"fs.azure.account.key.ilab9788543873.blob.core.windows.net":"TAyrrfaiCQ86vkgSXyStufowrMVdk4T45mVw6TNcFFJocR6pTXy6ZMSUUTeeh5FpNTsBVAbVqdwk+AStHA3x1g=="})

True

In [0]:
storage_account_name = "ilab9788543873"
container = "gold"
storage_account_key = "TAyrrfaiCQ86vkgSXyStufowrMVdk4T45mVw6TNcFFJocR6pTXy6ZMSUUTeeh5FpNTsBVAbVqdwk+AStHA3x1g=="

spark.conf.set(f"fs.azure.account.key.{storage_account_name}.blob.core.windows.net", storage_account_key)

merged_df.write.parquet(f"wasbs://{container}@{storage_account_name}.blob.core.windows.net/merged_df.parquet")